In [68]:
import pandas as pd
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.cluster import KMeans
import networkx as nx
import gensim
import itertools


In [25]:
# path to ConceptNet Numberbatch embeddings file
embeddings_file = 'datasets/numberbatch.txt'

# Load the word embeddings
def load_embeddings(file_path):
    embeddings = {}
    
    with open(file_path, 'r') as f:
        for line in f:
            parts = line.strip().split()
            word = parts[0]
            vector = np.array(parts[1:], dtype=np.float32)
            embeddings[word] = vector
    
    return embeddings

# Load the embeddings into a dictionary
embeddings = load_embeddings(embeddings_file)


In [30]:
embeddings

{'516782': array([300.], dtype=float32),
 '##': array([ 0.0295, -0.0405, -0.0341,  0.0837, -0.0575,  0.0482, -0.0145,
         0.0019,  0.0347,  0.0825, -0.0735,  0.0083, -0.0944, -0.0717,
         0.1994, -0.0107, -0.0783,  0.0693, -0.0161,  0.046 ,  0.1713,
         0.0727, -0.0983, -0.0641, -0.0124,  0.014 , -0.0473,  0.1162,
         0.1127, -0.0739, -0.0666, -0.0631, -0.0196, -0.0709, -0.0302,
        -0.1179,  0.0618,  0.0519,  0.0121,  0.0056,  0.0765,  0.0083,
         0.0142, -0.0883,  0.0255, -0.0015,  0.0748, -0.0214, -0.1229,
        -0.0017, -0.0317,  0.0062,  0.0191,  0.1199,  0.0969,  0.0471,
        -0.0436,  0.0068, -0.0418,  0.0152,  0.0222, -0.1094, -0.0128,
        -0.0608,  0.0089, -0.0595,  0.144 , -0.0798,  0.0247, -0.0462,
         0.1096,  0.088 , -0.012 , -0.0788, -0.0957, -0.0101, -0.0441,
         0.0881, -0.0223,  0.1191,  0.0082,  0.0629, -0.1335,  0.078 ,
        -0.13  ,  0.1064,  0.0998,  0.0302,  0.0443,  0.0002, -0.0337,
         0.0083,  0.0378,  0.0

In [3]:
# Print an example embedding
print(embeddings['dog'][:10])  # Display the first 10 dimensions of the "dog" embedding

[-0.0037 -0.0129  0.186  -0.032  -0.0958  0.071  -0.1087 -0.1043  0.0455
 -0.0187]


In [31]:
# Function to compute cosine similarity between two word vectors
def get_cosine_similarity(word1, word2, embeddings):
    vector1 = embeddings.get(word1)
    vector2 = embeddings.get(word2)
    
    if vector1 is None or vector2 is None:
        return 0
    
    vector1 = vector1.reshape(1, -1)
    vector2 = vector2.reshape(1, -1)
    
    return cosine_similarity(vector1, vector2)[0][0]

density: average cosine similarity INSIDE the group

conductance: average cosine similarity between members of the group and outsiders

normalize both (0-1) and then flip conductance (1 - conductance), then sum for the rank

In [58]:
# Computer similarity between words

# Load the pretrained Word2Vec model (Google News vectors or other model)
# Note: You can replace this path with the actual path to your model
model_path='GoogleNews-vectors-negative300.bin'
word2vec_model = gensim.models.KeyedVectors.load_word2vec_format(model_path, binary=True)

# Your list of words, including multi-word phrases
words = ["raven", "golfer", "pilot", "pendulum", "drum", "usher", "saloon doors", "cask", 
         "cowboy", "cylinder", "steer", "jet", "tank", "ram", "swing", "shepherd"]

# Function to get embedding for a single word or multi-word phrase
def get_embedding(word):
    if word in embeddings:
        # Return pre-existing embedding from the dictionary for single words
        return embeddings[word]
    else:
        # For multi-word phrases, split and average the embeddings of individual words
        words_in_phrase = word.split()  # Split phrase into words
        embeddings_list = []
        for w in words_in_phrase:
            if w in word2vec_model:  # Check if the word exists in the Word2Vec model
                embeddings_list.append(word2vec_model[w])
        if embeddings_list:
            # Average the embeddings of the words in the phrase
            return np.mean(embeddings_list, axis=0)
        else:
            # If no embeddings are found (e.g., out-of-vocabulary), return a zero vector
            return np.zeros(word2vec_model.vector_size)

# Create an empty graph
G = nx.Graph()

# Add nodes (words) to the graph
G.add_nodes_from(words)

# Compute the embeddings for each word or phrase
embedding_matrix = np.array([get_embedding(word) for word in words])

# Compute the cosine similarity matrix between word embeddings
cos_sim_matrix = cosine_similarity(embedding_matrix)

# Add edges between words based on cosine similarity
threshold = 0.1  # Set a threshold to consider only significant similarities
for i, word1 in enumerate(words):
    for j, word2 in enumerate(words):
        if i < j:  # Ensure each pair is considered once
            similarity = cos_sim_matrix[i, j]
            print(word1, word2)
            print(similarity)
            G.add_edge(word1, word2, weight=similarity)

# Now, G is a graph where each node is a word, and the edges represent cosine similarities


raven golfer
-0.1142686
raven pilot
0.14494799
raven pendulum
0.13649902
raven drum
0.020225527
raven usher
0.014211528
raven saloon doors
-0.07882634
raven cask
0.11268011
raven cowboy
0.07672058
raven cylinder
-0.07525745
raven steer
-0.01770095
raven jet
0.1278895
raven tank
-0.058420353
raven ram
0.05243879
raven swing
-0.012335028
raven shepherd
0.096116915
golfer pilot
0.056247137
golfer pendulum
0.049184304
golfer drum
0.04541753
golfer usher
0.04688858
golfer saloon doors
-0.07915447
golfer cask
-0.0153439
golfer cowboy
0.07295931
golfer cylinder
0.038528852
golfer steer
0.03928552
golfer jet
0.047182392
golfer tank
-0.036109503
golfer ram
-0.024710927
golfer swing
0.25599775
golfer shepherd
-0.05354227
pilot pendulum
0.02626811
pilot drum
-0.041934554
pilot usher
0.104296744
pilot saloon doors
0.023416638
pilot cask
0.022643825
pilot cowboy
0.024923299
pilot cylinder
0.028956743
pilot steer
0.2270476
pilot jet
0.47954142
pilot tank
0.11793737
pilot ram
-0.0396323
pilot swing
-

In [76]:
def compute_density(G, group):
    pairs = itertools.combinations(group, 2)  # Generate all unique pairs of nodes in the group
    similarities = []
    for word1, word2 in pairs:
        if G.has_edge(word1, word2):
            similarities.append(G[word1][word2]['weight'])
    return sum(similarities) / len(similarities) if similarities else 0

def compute_conductance(G, group, all_words):
    outsiders = [word for word in all_words if word not in group]  # Get nodes not in the group
    conductances = []
    for word_in_group in group:
        for word_outside in outsiders:
            if G.has_edge(word_in_group, word_outside):
                conductances.append(G[word_in_group][word_outside]['weight'])
    return sum(conductances) / len(conductances) if conductances else 0

def compute_rank(G, combo, connections):
    return compute_density(G, combo) + (1 - compute_conductance(G, combo, connections))


# Generate guesses
def generateGuesses(G, connections):
    combinations_of_4 = list(itertools.combinations(connections, 4))
    combos = []
    # Print the combos
    for combo in combinations_of_4:
        combos.append(combo)
    
    # Rank combinations
    combinations = dict()

    for combo in combos:
        # compute rank
        rank = compute_rank(G, combo, connections)

        #add to dictionary
        combinations[combo] = rank

    sorted_combinations = dict(sorted(combinations.items(), key=lambda item: item[1], reverse=True))

    return sorted_combinations

In [109]:
guess = generateGuesses(G, words)
guess

{('drum', 'cask', 'cylinder', 'tank'): 1.2331774359724175,
 ('cask', 'cylinder', 'jet', 'tank'): 1.229307591818118,
 ('pilot', 'cylinder', 'jet', 'tank'): 1.2017651397036389,
 ('cask', 'cylinder', 'tank', 'ram'): 1.2017221417627297,
 ('golfer', 'pendulum', 'drum', 'swing'): 1.1876535980166711,
 ('pendulum', 'drum', 'cylinder', 'swing'): 1.1804792045246966,
 ('pendulum', 'drum', 'usher', 'swing'): 1.1729507542525728,
 ('drum', 'cylinder', 'jet', 'tank'): 1.1693257240888975,
 ('golfer', 'pendulum', 'usher', 'swing'): 1.1619087970078301,
 ('pilot', 'cask', 'jet', 'tank'): 1.1614105447079055,
 ('pendulum', 'cask', 'cylinder', 'tank'): 1.1612386503547896,
 ('pendulum', 'usher', 'steer', 'swing'): 1.1570223369635642,
 ('pendulum', 'drum', 'steer', 'swing'): 1.1557906213468716,
 ('pendulum', 'drum', 'cask', 'swing'): 1.1537082752426309,
 ('pilot', 'cask', 'cylinder', 'tank'): 1.1500076837449644,
 ('cowboy', 'steer', 'ram', 'shepherd'): 1.1489157471902822,
 ('cask', 'cylinder', 'steer', 'tank'

In [110]:
new_words = [word for word in words if word not in next(iter(guess))]

guess = generateGuesses(G, new_words)
guess

{('golfer', 'pendulum', 'usher', 'swing'): 1.1711366440965019,
 ('pendulum', 'usher', 'steer', 'swing'): 1.1627636888588313,
 ('golfer', 'pendulum', 'steer', 'swing'): 1.1570299362501828,
 ('cowboy', 'steer', 'ram', 'shepherd'): 1.1554036759916926,
 ('golfer', 'pendulum', 'jet', 'swing'): 1.1327060549277423,
 ('golfer', 'pendulum', 'cowboy', 'swing'): 1.132703077950282,
 ('pilot', 'pendulum', 'jet', 'swing'): 1.1287938939785818,
 ('pilot', 'usher', 'steer', 'jet'): 1.1277028276769367,
 ('usher', 'cowboy', 'steer', 'shepherd'): 1.1245805337966885,
 ('raven', 'pilot', 'pendulum', 'jet'): 1.1213220677212423,
 ('raven', 'pilot', 'steer', 'jet'): 1.118711483082734,
 ('pilot', 'usher', 'steer', 'shepherd'): 1.1182178734403958,
 ('raven', 'pendulum', 'usher', 'swing'): 1.1181140762249318,
 ('raven', 'golfer', 'pendulum', 'swing'): 1.1178479346708627,
 ('pilot', 'cowboy', 'steer', 'shepherd'): 1.116304277292026,
 ('pendulum', 'cowboy', 'steer', 'swing'): 1.113804681682571,
 ('raven', 'pilot', 

In [111]:
# Find the subset with the highest rank when one word is removed
def find_highest_rank(G, connections):
    max_density = float('-inf')
    max_conductance = float('-inf')
    best_subset = None
    weakest_link = None
    
    # Generate all combinations of removing one word (subsets of 3)
    for subset in itertools.combinations(connections, len(connections) - 1):
        density = compute_density(G, subset)
        conductance = compute_conductance(G, subset, connections)
        if density > max_density or conductance > max_conductance:
            max_density = density
            max_conductance = conductance
            best_subset = subset
            # The weakest link is the word removed to form the current subset
            weakest_link = list(set(connections) - set(subset))[0]
    
    return best_subset, weakest_link

# Function to find the highest rank by adding one unused word to the best subset
def find_best_addition(G, best_subset, connections, weakest_link, previous_guesses):
    unused_words = [word for word in connections if word not in best_subset and word != weakest_link]
    
    max_density = float('-inf')
    max_conductance = float('-inf')
    best_combination = None
    
    for word in unused_words:
        new_group = list(best_subset) + [word]
        density = compute_density(G, best_subset)
        conductance = compute_conductance(G, best_subset, connections)
        if (density > max_density or conductance > max_conductance) and (sorted(new_group) not in [sorted(previous_guess) for previous_guess in previous_guesses]):
            max_density = density
            max_conductance = conductance
            max_rank = density + (1-conductance)
            best_combination = new_group
    
    return best_combination, max_rank

def isOneAway(G, guess, new_words, previous_guesses):
    weakest_link_removed, weakest_link = find_highest_rank(G, next(iter(guess)))
    best_combination, rank = find_best_addition(G, weakest_link_removed, new_words, weakest_link, previous_guesses)

    return best_combination, rank

In [112]:
previous_guesses = [next(iter(guess))]
new_guess = isOneAway(G, guess, new_words, previous_guesses)
new_guess

(['pendulum', 'usher', 'swing', 'raven'], 1.2253767453065074)

In [113]:
previous_guesses.append(next(iter(new_guess)))
next_guess = isOneAway(G, new_guess, new_words, previous_guesses)
next_guess

(['usher', 'swing', 'raven', 'golfer'], 0.9693968296913361)